In [1]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from hazm import Normalizer, Lemmatizer, word_tokenize
from cleantext import clean

import pandas as pd
import numpy as np
import re
import json
import faiss
import time

Since the GPL-licensed package `unidecode` is not installed, using Python's `unicodedata` package which yields worse results.


In [2]:
df_nickname = pd.read_csv('nicknames.csv')

In [3]:
df_nickname

nick_name
0                       NaN
1          ‌ ‌ ‌ ‌ ‌ ‌ ‌ ‌?
2           ‌ ‌ ‌- emilia<3
3        ⁭⁫⁪⁫⁬⁭⁫⁪⁫⁬ ⁭hop_pa
4                     ‌ (Z)
...                     ...
141246        𝓜𝓸𝓱𝓪𝓶𝓶𝓪𝓭 𝓡𝓮𝔃𝓪
141247         🤍🖤🤎💜💙💚💛🧡⁦❤️⁩
141248            𝐌𝐚𝐫𝐳𝐢𝐲𝐞𝐡🌱
141249           𝓐𝓶𝓲𝓻𝓱𝓸𝓼𝓮𝓲𝓷
141250          𝒎𝒂𝒉𝒅𝒐𝒌𝒉𝒕𝒂𝒓𝒚

[141251 rows x 1 columns]

In [4]:
df_nickname.dropna(inplace=True)

In [5]:
def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', raw_html)
    return cleantext


def cleaning(text):
    text = text.strip()

    # regular cleaning
    text = clean(text,
      fix_unicode=True,
      to_ascii=False,
      lower=True,
      no_line_breaks=True,
      no_urls=True,
      no_emails=True,
      no_phone_numbers=True,
      no_numbers=False,
      no_digits=False,
      no_currency_symbols=True,
      no_punct=False,
      replace_with_url="",
      replace_with_email="",
      replace_with_phone_number="",
      replace_with_number="",
      replace_with_digit="0",
      replace_with_currency_symbol="",
    )

    # cleaning htmls
    text = cleanhtml(text)

    # normalizing
    normalizer = Normalizer()
    text = normalizer.normalize(text)

    # removing wierd patterns
    wierd_pattern = re.compile("["
      u"\U0001F600-\U0001F64F"  # emoticons
      u"\U0001F300-\U0001F5FF"  # symbols & pictographs
      u"\U0001F680-\U0001F6FF"  # transport & map symbols
      u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
      u"\U00002702-\U000027B0"
      u"\U000024C2-\U0001F251"
      u"\U0001f926-\U0001f937"
      u'\U00010000-\U0010ffff'
      u"\u200d"
      u"\u2640-\u2642"
      u"\u2600-\u2B55"
      u"\u23cf"
      u"\u23e9"
      u"\u231a"
      u"\u3030"
      u"\ufe0f"
      u"\u2069"
      u"\u2066"
      # u"\u200c"
      u"\u2068"
      u"\u2067"
      "]+", flags=re.UNICODE)

    text = wierd_pattern.sub(r'', text)

    # removing extra spaces, hashtags
    text = re.sub("#", "", text)
    text = re.sub("\s+", " ", text)

    return text

In [6]:
df_nickname['nick_name'] = df_nickname['nick_name'].astype(str)
df_nickname['preprocessed_nickname'] = df_nickname['nick_name'].apply(cleaning)

In [7]:
df_nickname

nick_name preprocessed_nickname
1          ‌ ‌ ‌ ‌ ‌ ‌ ‌ ‌?      ‌ ‌ ‌ ‌ ‌ ‌ ‌ ‌?
2           ‌ ‌ ‌- emilia<3       ‌ ‌ ‌- emilia<۳
3        ⁭⁫⁪⁫⁬⁭⁫⁪⁫⁬ ⁭hop_pa                hop_pa
4                     ‌ (Z)                 ‌ (z)
5                   ‍ Azita                 azita
...                     ...                   ...
141246        𝓜𝓸𝓱𝓪𝓶𝓶𝓪𝓭 𝓡𝓮𝔃𝓪                      
141247         🤍🖤🤎💜💙💚💛🧡⁦❤️⁩                      
141248            𝐌𝐚𝐫𝐳𝐢𝐲𝐞𝐡🌱                      
141249           𝓐𝓶𝓲𝓻𝓱𝓸𝓼𝓮𝓲𝓷                      
141250          𝒎𝒂𝒉𝒅𝒐𝒌𝒉𝒕𝒂𝒓𝒚                      

[141248 rows x 2 columns]

In [8]:
df_en = pd.read_csv('clean_data.csv')
df_fa = pd.read_csv('clean_data_fa.csv')
df_sw = pd.read_csv('swear_words.csv')

In [9]:
df_offensive = pd.concat([df_en, df_fa, df_sw], ignore_index=True)

In [10]:
model = SentenceTransformer('sentence-transformers/distiluse-base-multilingual-cased-v2')

In [11]:
def embed(sentences):
    embeddings = model.encode(sentences)
    embeds = []

    #Print the embeddings
    for sentence, embedding in zip(sentences, embeddings):
        embeds.append(embedding)
    
    return embeds

In [14]:
sentences = df_offensive[df_offensive['is_offensive'] == 1]['text'].astype(str).tolist()

In [15]:
offensive_sentences = model.encode(sentences)

In [16]:
# Create an index using FAISS
index = faiss.IndexFlatL2(offensive_sentences.shape[1])
index.add(offensive_sentences)
faiss.write_index(index, 'index_offensive_sentences')
index = faiss.read_index('index_offensive_sentences')

In [34]:
def search(query):
    query_vector = model.encode([query])
    k = 5
    top_k = index.search(query_vector, k)
    top_k_indexs = top_k[1].tolist()[0]
    most_similar_sentenc = sentences[top_k_indexs[0]]
    mss_vector = model.encode([most_similar_sentenc])
    score = cosine_similarity(query_vector, mss_vector)
    print(score)
    min_dist = top_k[0].min()
    print(top_k[0][0])
    print([sentences[_id] for _id in top_k_indexs])
    if min_dist < 0.1:
        return 1
    return 0

In [41]:
search('milf')

[[0.99999994]]
[1.13286496e-13 1.13286496e-13 1.00285433e-01 1.22539036e-01
 1.32514834e-01]
['milf', 'milf', "mf'ing", 'mfs', "mf'er"]


1

In [ ]:
df_nickname['is_offensive'] = df_nickname['nick_name'].apply(search)

[[0.90170676]]
[0.08189503 0.0899078  0.10502955 0.10679785 0.10812879]
['pohm', 'چس', 'cumz', 'ky', 'asian']
[[0.61331046]]
[0.1870726  0.18975332 0.19257471 0.19573517 0.19993013]
['ar5e', '    شت ریحان :)))))', 'ku kluxer', 'لجن', 'kyke']
[[0.7618462]]
[0.4126373  0.41323662 0.4180944  0.41884086 0.4202758 ]
['pimp', 'perv', 'peepshpw', 'dipsh1tty', 'pudd']
[[0.70472014]]
[0.3330533  0.34329194 0.34389296 0.35138577 0.35303375]
['d!ldo', 'd!ld0', 'd!ck', 'BJ', 'd!cks']
[[0.93181336]]
[0.049444   0.07739462 0.07775395 0.08193885 0.08503124]
['azz', 'jism', 'tit', 'آلت', 'kunt']
[[0.758118]]
[0.3175879  0.40322375 0.40647253 0.40966085 0.41047132]
['douche', 'حشری', 'dive', 'nambla', 'wetspot']
[[0.87353003]]
[0.10087565 0.11381803 0.11683663 0.12250811 0.12423525]
['بیابخورش', 'babeland', 'bender', 'bizzach', 'bastid']
[[0.8680396]]
[0.15292327 0.16231191 0.1808975  0.19911423 0.20004794]
['داف', 'felch', 'faggs', 'futhamucka', 'fookuh']
[[0.90157384]]
[0.07313654 0.07313654 0.075545

[[0.64277637]]
[0.2548421  0.26361158 0.2717267  0.28651434 0.28689912]
[' عحب جنده ایه :~', ' واسه من گه اورگانیکه. :))))))))))', ' قشنگ ریدی تو دکلمه :)))', ' وای دقیقا بچگیام همین\u200cو میخوندن برام پشمام :))))))))', ' اینو\u200c کی\u200c گاییدم :))))))']
[[0.78036433]]
[0.20927933 0.23833275 0.23896164 0.24221402 0.24993579]
['satan', 'devil', ' دیوس 😅😍😅', 'کصخل', 'لخت']
[[0.87659514]]
[0.16324988 0.16880408 0.17582086 0.1758738  0.19214226]
['whiz', 'whash', 'k..!ke', 'k!ke', 'pohm']
[[0.6098381]]
[0.38488263 0.40403715 0.40445858 0.407483   0.41866738]
['fat', ' دیوس :))))))', '   گوزو :))))))))', ' اینو\u200c کی\u200c گاییدم :))))))', ' نکبت وطنی :))))))']
[[0.80122274]]
[0.20214887 0.20954299 0.24094808 0.2584846  0.26089287]
['لز', 'لر', 'کص لیس', 'limy', 'آلت']
[[0.8344767]]
[0.16355398 0.167822   0.18155378 0.18334308 0.18901008]
['pohm', 'پشمام :)))))) ', 'whiz', 'شهوتی', ' پشمام :))))))))']
[[0.7737483]]
[0.3530926  0.3573035  0.43027443 0.4448175  0.4478368 ]
['xx', 'xxx

[[0.6802357]]
[0.40038416 0.4156146  0.43304557 0.43330085 0.46446818]
[' ممه هامی :**', '  نگاییدم :**', ' خایه مال*', ' نگاییدم :*', 'g0ddamnit']
[[0.7961771]]
[0.23485988 0.2384773  0.2551491  0.25534827 0.2567442 ]
['  نگاییدم :**', 'pohm', 'k..!ke', ' شت اصن :(عاره ^_____^ ایشالا', ' خایه مال*']
[[0.7921759]]
[0.21758911 0.21919885 0.228762   0.23023984 0.23036744]
['  نگاییدم :**', ' ممه هامی :**', 'pom', 'ky', 'kum']
[[0.7518569]]
[0.36981422 0.37076795 0.38932166 0.39423224 0.39721027]
['c*nty', '  نگاییدم :**', ' خایه مال*', ' نگاییدم :*', ' ممه هامی :**']
[[0.734063]]
[0.3772073  0.3994427  0.40037876 0.4191011  0.42325762]
['ریدی', ' رید', 'لر', 'ky', 'kum']
[[0.75623554]]
[0.34328324 0.35104704 0.3683957  0.37328815 0.37669393]
['  نگاییدم :**', 'k..!ke', ' خایه مال*', ' نگاییدم :*', 'c*nty']
[[0.86198735]]
[0.19378638 0.2407983  0.2520031  0.25581938 0.26133013]
['w4nk3r', 'w4nker', 's_h_i_s', 's_h_i_', 'f_u_c_k']
[[0.7160856]]
[0.39980984 0.39980984 0.41005483 0.41393626 

[[0.67633605]]
[0.3506179  0.3508918  0.35453007 0.35532203 0.36308956]
['k1ke', 'f@g', 'fag0t', 'f@k', 'g0ddamnit']
[[0.7712361]]
[0.2564915  0.25853872 0.26557252 0.28912866 0.29681608]
['w4nk3r', 'n1gg@', 'c0xux0r', 'nobj0key', 'm0ng0l0id']
[[0.8076536]]
[0.2773707  0.27880532 0.2811893  0.29163224 0.31093502]
['c*nty', ' نگاییدم :*', '  نگاییدم :**', ' ممه هامی :**', 'c*nt']
[[0.8479941]]
[0.17902179 0.18039171 0.19787511 0.2047126  0.20810407]
['pohm', 'ho', 'whiz', 'k..!ke', 'c*nt']
[[0.69643664]]
[0.30933607 0.3107676  0.31712872 0.32026017 0.32967466]
['kums', 'g0ddamnit', ' ممه هامی :**', 'kum', 'g0ddamn']
[[0.7868733]]
[0.29865196 0.30462152 0.30462152 0.30479762 0.3056345 ]
['jiga', 'dong', 'dong', 'honk', 'phuku']
[[0.85476613]]
[0.2661492 0.3177313 0.3201587 0.3516102 0.3531382]
['s_h_i_', 's_h_i_s', 'c*nty', 'ho', 'c*nts']
[[0.7253493]]
[0.29314116 0.29328662 0.29331774 0.2947802  0.29690957]
['phuku', ' شت اصن :(عاره ^_____^ ایشالا', 'hobo', 'pohm', 'ho']
[[0.62282217]]


[[0.8464167]]
[0.29349643 0.29795802 0.3106763  0.31445473 0.32108814]
['s_h_i_', 's_h_i_s', 'm0fo', 'a_s_s', 'm0f0']
[[0.7086873]]
[0.3503171  0.37593552 0.39793104 0.40153387 0.4041866 ]
['n1gg@', 'g@yshit', 'w4nk3r', 'g@y b1tch', 'n1gg3r']
[[0.7829054]]
[0.3115957  0.3225412  0.32562897 0.3285526  0.33326647]
['n1gg@', 'n1gga', 'nigg', 'n1ggas', 'n1gguh']
[[0.75827956]]
[0.2903711  0.2991745  0.30317312 0.30616385 0.31247216]
['n1gguh', 'n1gga', 'ky', 'c*nt', 'g0ddamn']
[[0.85971916]]
[0.25317395 0.25850728 0.26594514 0.27834612 0.28891218]
['s_h_i_', 'c*nt', 'c*nty', 'c*nts', 'n1gga']
[[0.8160456]]
[0.23553361 0.24503234 0.24835472 0.24871983 0.2501705 ]
['c*nt', 'n1gguh', 'nikkas', 'n1gga', 'nickas']
[[0.71557325]]
[0.47591138 0.47816744 0.48773578 0.5018401  0.50805855]
['c*nt', 'a_s_s', 'n1gg@', 's_h_i_', 'n0bj0cky']
[[0.8953243]]
[0.19877936 0.20325807 0.21479954 0.24529752 0.3271711 ]
['a_s_s', 's_h_i_', 's_h_i_s', 'f_u_c_k', 'n1gg@']
[[0.8044735]]
[0.35904068 0.41852045 0.423

...

[[0.9333228]]
[0.03566022 0.03609094 0.03855371 0.03855371 0.03903162]
['knobendz', 'kinbaku', 'puss', 'puss', 'turd']
[[0.8210943]]
[0.09967931 0.10085177 0.1034732  0.10349928 0.10374814]
['kinkster', 'bizzach', ' زنیکه پتیاره', ' کص گفتم😂', 'knobendy']
[[0.6257744]]
[0.28800613 0.3041305  0.3106435  0.31115526 0.3209295 ]
[' کیر توش🙂', 'کیرمکیدن', ' گلدین هیز', '   کیری 😔', ' کیروش کیریه']
[[0.9408908]]
[0.02974005 0.02990967 0.02990967 0.03028342 0.03093567]
['tinkle', 'kyke', 'kyke', 'کص', 'kum']
[[0.8039863]]
[0.09897708 0.11642043 0.11642043 0.11642043 0.11642046]
[' کیر توش🙂', 'به کیرم ', ' به کیرم', 'به کیرم', ' به کیرم']
[[0.9031511]]
[0.06296546 0.06297329 0.06637615 0.06792744 0.06800185]
['kinbaku', 'wuzzie', 'knobendz', 'tinkle', 'pisspig']
[[0.7592237]]
[0.30722925 0.34373274 0.3437329  0.3510428  0.36835876]
['glazeddonut', 'skanky', 'skanky', 'groe', 'lezzo']
[[0.89145863]]
[0.08290902 0.09881076 0.10786977 0.10848697 0.11182688]
['گوز', 'گاییدن', 'گیخوار', 'jigro', 'h

[[0.9347104]]
[0.07991491 0.13028662 0.14209764 0.15544187 0.17336836]
['pocha', 'poo', 'bi', 'sandm', 'bast']
[[0.86931646]]
[0.15169305 0.15191606 0.16409385 0.17568445 0.1938713 ]
['گوزو', 'jigro', 'ginzo', 'jigaboo', 'jigga']
[[0.89684063]]
[0.09427042 0.10617489 0.11158232 0.11404277 0.1242972 ]
['jigro', 'گوز', 'gonzagas', 'گاییدن', 'گایدن']
[[0.9142206]]
[0.08750494 0.09895759 0.10449181 0.10647313 0.10760966]
['گوز', 'گاییدن', 'argie', 'گایدی', 'گوزو']
[[0.8993936]]
[0.06718868 0.08663185 0.08726746 0.08729039 0.089201  ]
['آشغال', 'کردنی', 'زارت', 'درازگوش', 'knobendz']
[[0.7175046]]
[0.29765147 0.31952837 0.33814722 0.3437158  0.35837895]
['fag0t', 'n1g3rz', 'fagg0t', 'g0ddamned', 'ar5e']
[[0.91878736]]
[0.12185414 0.13296059 0.16287115 0.17140424 0.17204136]
['fvck', 'fvcka', 'bwc', 'fcka', 'fvcker']
[[0.96505094]]
[0.05454188 0.08276238 0.11054052 0.11449142 0.1156287 ]
['wtf', 'fck', 'mfk', 'gipp', 'nymph']
[[0.9621017]]
[0.0629262  0.08589396 0.08589396 0.09559113 0.10564

[[0.878047]]
[0.20347267 0.21724959 0.21724959 0.21951693 0.22363168]
['wog', 'gyp', 'gyp', 'wn', 'gob']
[[0.80285704]]
[0.20989151 0.21658161 0.22599411 0.22909513 0.23111312]
['سگی', 'باسنی', 'خز', 'سیکیم', 'شهوتی']
[[0.92259026]]
[0.12685472 0.13589647 0.17119107 0.17716898 0.17716898]
['wog', 'wtf', 'fck', 'wop', 'wop']
[[0.7572936]]
[0.32370052 0.32370052 0.32503742 0.33059877 0.33954218]
[' هیز', 'هیز', 'خز', 'g0ddamn', 'xtc']
[[0.87167025]]
[0.19927779 0.20288645 0.20288645 0.2158413  0.21773943]
['wn', 'twat', 'twat', "f'er", 'wtf']
[[0.9282086]]
[0.0607522  0.06109139 0.06236499 0.06688607 0.07387723]
['vag', 'کص خل', ' هلی شت', 'کوص خل', 'goyim']
[[0.7948868]]
[0.14772198 0.15243971 0.15933943 0.16473502 0.16527387]
['گاییده', 'گاییدن', 'گیخوار', 'لجن', 'kyke']
[[0.8354534]]
[0.16385528 0.16822824 0.17090824 0.18543956 0.18552333]
['jew', 'gin', 'azz', 'g0ddamn', 'jigro']
[[0.92824423]]
[0.04694562 0.0532918  0.06140911 0.0620995  0.06499282]
['گاییده', 'زنیکه', 'کص خل', 'لخت

[[0.7962786]]
[0.28111297 0.28822267 0.29922426 0.30256134 0.30277354]
['jigro', 'whigger', 'gonzagas', 'jiggabu', 'jigaboos']
[[0.8394446]]
[0.2560239  0.26907936 0.27190548 0.2742182  0.2755112 ]
['geebag', 'gubba', 'jigaboos', 'gob', 'whigger']
[[0.70345056]]
[0.38783976 0.38897783 0.3949479  0.3963551  0.4010498 ]
['muddafukkas', 'muthafukka', 'shawtypimp', 'shiat', ' کامبیز ریدی']
[[0.7394742]]
[0.37132648 0.3750835  0.3836286  0.4049187  0.41335216]
['jigro', 'vietcong', 'jiggabu', 'jigaboos', 'jiggaboos']
[[0.8621634]]
[0.1411874  0.15075362 0.15179288 0.15200609 0.15576127]
['ملنگ', 'gonzagas', 'hamas', 'jigro', 'argie']
[[0.8421317]]
[0.1787708  0.19559354 0.20283946 0.20334405 0.20640928]
['jigro', 'hamas', 'jigaboos', 'ملنگ', 'gonzagas']
[[0.85018647]]
[0.23905516 0.26293164 0.26877004 0.27675027 0.28628314]
['higga', 'whigger', 'muthafukka', 'hamas', 'muthafucka']
[[0.75116384]]
[0.36714432 0.41399813 0.43787768 0.44038537 0.45378977]
['HA GAAAAAAAAAYYYYY', 'jigro', ' گلدین

[[0.7735443]]
[0.35284692 0.3828604  0.38465527 0.39279997 0.40491283]
['jiggabu', 'jigro', 'jigaboos', 'jiggaboos', 'vietcong']
[[0.84632784]]
[0.16749948 0.17471874 0.17632318 0.21114215 0.21568502]
['niga', 'nonce', 'nuke', 'nikker', 'nip']
[[0.5129925]]
[0.5541752  0.579953   0.6108001  0.61606    0.62470245]
['g@yshit', 'g@y b1tch', 'g@ylord', '0rg@sm', 'g0ddamned']
[[0.8073598]]
[0.28647816 0.30319023 0.30948383 0.32506654 0.32583156]
['jigaboos', 'jiggabu', 'jigro', 'jiggas', 'jiggaboos']
[[0.7217641]]
[0.42146054 0.4336662  0.43671614 0.44371295 0.4493246 ]
['higg3r', 'n1ggah', 'jigro', 'g@yshit', 'n1ggas']
[[0.8542277]]
[0.20601565 0.22139473 0.23642075 0.258223   0.25872555]
['jiggabu', 'jigro', 'jigaboos', 'jiggas', 'jiggabo']
[[0.88396]]
[0.11448359 0.14869109 0.16379112 0.16391441 0.17721298]
['jigro', 'gonzagas', 'jigaboos', 'گوز', 'argie']
[[0.87192]]
[0.17683989 0.17841026 0.17860556 0.18395609 0.19184792]
['jigaboos', 'higga', 'mggor', 'jigro', 'geezer']
[[0.8985599]]
